In [1]:
from decoder_new import *
from encoder import *
from data_loader import *
import pickle
import random
import torch.optim as optim
from torch.autograd import Variable
import csv
import time
from tqdm import tqdm
import gc
import os
import torchvision.transforms as tf
import json
from torch.nn.utils.rnn import pack_padded_sequence
from nltk.translate.bleu_score import corpus_bleu


[nltk_data] Downloading package punkt to
[nltk_data]     /datasets/home/62/762/ajabaren/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:


def validate(val_loader, encoder, decoder, criterion, maxSeqLen, vocablen, use_gpu = True, calculate_bleu = True):

    
    #Evaluation Mode
    decoder.eval()
    encoder.eval()

    
    references = list()
    hypotheses = list() 
    
    if use_gpu:
        device = torch.device("cuda:0")
        
        
    with torch.no_grad():
        
        count    = 0
        loss_avg = 0
        bleu1_avg = 0
        bleu4_avg = 0
        
        for i, (imgs, caps, caplens, allcaps) in enumerate(val_loader):

            # Move to device, if available
            if use_gpu:
                imgs = imgs.to(device)
                caps = caps.to(device)
            #print('type(caps): ',type(caps))
            #caps_copy = caps
            
            
            if (i % 10000) == 0: #TODO drop
                print('i: ',i)
                print('imgs: ',imgs)
                print('caps: ',caps)
                print('val_loader: ', val_loader)
                print('caplens: ',caplens)
            
            enc_out = encoder(imgs)
            actual_lengths = allcaps
            
            
            
            temperature = 1
            test_pred = decoder.generate_caption(enc_out, maxSeqLen, temperature)

            test_pred_sample = test_pred[0].cpu().numpy()          

            
            '''
            if i % 100 == 0:
                # Convert word_ids to words
                sampled_caption = []
                for word_id in test_pred_sample:
                    word = vocab.idx2word[word_id]
                    sampled_caption.append(word)
                    if word == '<end>':
                        break
                sentence = ' '.join(sampled_caption)
                #hypotheses.append(sampled_caption)
                print ('sentence: ',sentence)            
                print(type(sampled_caption))        
                print(sampled_caption)        
                print('len(generated_sentence): ',len(sampled_caption))
            '''    

            
            #Build a list of the predicted sentences
            # Convert word_ids to words
            sampled_caption = []
            #print('type(test_pred_sample: ', type(test_pred_sample))
            #print('test_pred_sample: ', test_pred_sample)
            for word_id in test_pred_sample:
                word = vocab.idx2word[word_id]
                sampled_caption.append(word)
                if word == '<end>':
                    break
            sentence = ' '.join(sampled_caption)
            hypotheses.append(sampled_caption)                
            if i % 100 ==0:
                print ('sentence: ',sentence)            
                print(type(sampled_caption))        
                print(sampled_caption)        
                print('len(generated_sentence): ',len(sampled_caption))
                
                
            
            # might drop
            '''
            for b in range(batch_size):
                flag = False
                for wi in range(maxSeqLen):
                    if test_pred[b, wi] == 2:
                        flag = True
                    if flag:
                        test_pred[b, wi] = 0
            
            if i % 1000 == 0:
                print('VAL: test pred: ', test_pred)
                print('VAL: test pred shape: ', test_pred.size())
            '''
                
            #targets = pack_padded_sequence(labels, lengths, batch_first=True)[0]
        
            outputs = decoder(caps, enc_out, actual_lengths)
            if i % 1000 == 0:
                print('VAL: outputs shape: ', outputs.size())
            new_outputs = torch.zeros(batch_size, maxSeqLen, vocablen)
            for dim in range(maxSeqLen):
                for b in range(batch_size):
                    new_outputs[b, dim, 0] = 1.0
            new_outputs[:, :(outputs.shape[1]), :] = outputs
            new_outputs = new_outputs.permute(0, 2, 1).to(device)
            
            #del inputs

            
            loss = criterion(new_outputs, Variable(caps.long()))
#            loss = criterion(outputs, targets)
            loss_avg += loss
            count+=1
            
            #del outputs            
            
            print('VAL: loss: ', loss)


                
            # References
            '''
            #allcaps = allcaps[sort_ind]  # because images were sorted in the decoder
            print('DBG: allcaps')
            print(allcaps)
            print(allcaps[0])
            print(allcaps[1])
            print(allcaps)
            
            print(type(caps))
            print('caps: ', caps)
            #print('caps_copy: ', caps_copy)
            '''
            
            
            
            caps_array = caps.cpu().numpy()  
            # Convert word_ids to words
            reference_caption = []
            sampled_caption = []
            
            for word_id in caps_array[0]:
                word = vocab.idx2word[word_id]
                reference_caption.append(word)
                if word == '<end>':
                    break
            ref_sentence = ' '.join(reference_caption)
            print('ref_sentence: ', ref_sentence)
            print('len(ref_sentence): ',len(reference_caption))
            references.append(reference_caption)   
            
            
            
            '''
            for j in range(len(allcaps)):
                img_caps = allcaps[j]#.tolist()
                img_captions = list(
                    map(lambda c: [w for w in c if w not in {word_map['<start>'], word_map['<pad>']}],
                        img_caps))  # remove <start> and pads
                references.append(img_captions)
            print('references: ', references)
            
            # Hypotheses
            #_, preds = torch.max(scores_copy, dim=2)
            outputs = outputs.tolist()
            temp_preds = list()
            for j, p in enumerate(outputs):
                temp_preds.append(outputs[j][:decode_lengths[j]])  # remove pads
            outputs = temp_preds
            hypotheses.extend(outputs)
            print('hypotheses: ', hypotheses)
            '''
           

        
        
            #print('len(references)', len(references))
            #print('len(hypotheses)', len(hypotheses))
            #print('references: ', references)
            #print('hypotheses: ', hypotheses)
        

            # Calculate BLEU-4 scores
            if calculate_bleu:
                bleu4 = corpus_bleu(references, hypotheses)                
                bleu1 = corpus_bleu(references, hypotheses,weights=(1.0, 0, 0, 0))
                print('bleu4: ', bleu4)        
                print('bleu1: ', bleu1)  
                bleu4_avg+=bleu4
                bleu1_avg+=bleu1
            
            del caps
            del outputs            
            
            
            if i % 100 == 0:
                break
                
                
        if calculate_bleu:
            loss_avg  = loss_avg/count
            bleu4_avg = bleu4_avg/count
            bleu1_avg = bleu1_avg/count 
            print('VAL: loss_avg: ', loss_avg)
            print('VAL: bleu4_avg: ', bleu4_avg)
            print('VAL: bleu1_avg: ', bleu1_avg)
        
        
        
        
            
    return loss_avg

In [3]:
def trainEncoderDecoder(encoder, decoder, criterion, epochs,
                        train_loader,val_loader, test_loader, name, batch_size, maxSeqLen, vocablen):
    
    #Create non-existing logfiles
    logname = './logs/' + name + '.log'
    i = 0
    if os.path.exists(logname) == True:
        
        logname = './logs/' + name + str(i) + '.log'
        while os.path.exists(logname):
            i+=1
            logname = './logs/' + name + str(i) + '.log'

    print('Loading results to logfile: ' + logname)
    with open(logname, "w") as file:
        file.write("Log file DATA: Validation Loss and Accuracy\n") 
    
    logname_summary = './logs/' + name + '_summary' + str(i) + '.log'    
    print('Loading Summary to : ' + logname_summary) 
    
    parameters = list(encoder.parameters())
    parameters.extend(list(decoder.parameters()))
    optimizer = optim.Adam(parameters, lr=5e-5)
    use_gpu = torch.cuda.is_available()
    if use_gpu:
        device = torch.device("cuda:0")
#         encoder = torch.nn.DataParallel(encoder)
#         decoder = torch.nn.DataParallel(decoder)
        
        encoder.to(device)
        decoder.to(device)
        
        
    
    val_loss_set = []
    val_acc_set = []
    val_iou_set = []
    
    
    training_loss = []
    
    # Early Stop criteria
    minLoss = 1e6
    minLossIdx = 0
    earliestStopEpoch = 10
    earlyStopDelta = 5
    for epoch in range(epochs):
        ts = time.time()
    
        for element in enumerate(train_loader):
            print('DEBUG: ', element)
            break
        #import pdb; pdb.set_trace()                     
        for iter, (inputs, labels, lengths, actual_lengths) in tqdm(enumerate(train_loader)):
            print('inp shape: ', inputs.shape)
#             print("Inputs:")
#             print(inputs)
            
            print("Labels")
            print(labels)
            print('labels shape: ', labels.shape)
            print("lengths: ", lengths)
            print("lengths shape: ", len(lengths))
            print("actual_lengths: ", actual_lengths)
            print("actual_lengths shape: ", len(actual_lengths))
            optimizer.zero_grad()
            
            
            encoder.train()
            decoder.train()
            
            if use_gpu:
                inputs = inputs.to(device)# Move your inputs onto the gpu
                labels = labels.to(device) # Move your labels onto the gpu
            
                
#             outputs = model(inputs)
            enc_out = encoder(inputs)
            print('enc out shape: ', enc_out.size())
        
            temperature = 1
            test_pred = decoder.generate_caption(enc_out, maxSeqLen, temperature)
            for b in range(batch_size):
                flag = False
                for wi in range(maxSeqLen):
                    if test_pred[b, wi] == 2:
                        flag = True
                    if flag:
                        test_pred[b, wi] = 0
            print('test pred: ', test_pred)
            print('test pred shape: ', test_pred.size())
            
            targets = pack_padded_sequence(labels, lengths, batch_first=True)[0]
            
            
            outputs = decoder(labels, enc_out, actual_lengths) #calls forward
            print('outputs shape: ', outputs.size())
            new_outputs = torch.zeros(batch_size, maxSeqLen, vocablen)
            for dim in range(maxSeqLen):
                for b in range(batch_size):
                    new_outputs[b, dim, 0] = 1.0
            new_outputs[:, :(outputs.shape[1]), :] = outputs
            new_outputs = new_outputs.permute(0, 2, 1).to(device)
            #del inputs
            
            print('outputs.shape:     ', outputs.shape)
            print('new_outputs.shape: ', new_outputs.shape)
            print('targets.shape: ', targets.shape)
            
            loss = criterion(new_outputs, Variable(labels.long()))
#            loss = criterion(outputs, targets)
            del labels
            del outputs

            loss.backward()
            loss = loss#.item()
            optimizer.step()

            if iter % 1 == 0:
                print("epoch{}, iter{}, loss: {}".format(epoch, iter, loss))
            
            if iter >=10:
                break

        
        # calculate val loss each epoch
        val_loss  = validate(val_loader, encoder, decoder, criterion,maxSeqLen, vocablen, use_gpu)
        val_loss_set.append(val_loss)

        
#         print("epoch {}, time {}, train loss {}, val loss {}, val acc {}, val iou {}".format(epoch, time.time() - ts,
#                                                                                                loss, val_loss,
#                                                                                                val_acc,
#                                                                                                val_iou))        
        training_loss.append(loss)
        
        with open(logname, "a") as file:
            file.write("writing!\n")
            file.write("Finish epoch {}, time elapsed {}".format(epoch, time.time() - ts))
            file.write("\n training Loss:   " + str(loss.item()))
#             file.write("\n Validation Loss: " + str(val_loss_set[-1]))
#             file.write("\n Validation acc:  " + str(val_acc_set[-1]))
#             file.write("\n Validation iou:  " + str(val_iou_set[-1]) + "\n ")                                             
                                                                                                
                                                                                                
        
        # Early stopping
#         if val_loss < minLoss:
#             # Store new best
#             torch.save(model, name)
#             minLoss = val_loss#.item()
#             minLossIdx = epoch
            
        # If passed min threshold, and no new min has been reached for delta epochs
#         elif epoch > earliestStopEpoch and (epoch - minLossIdx) > earlyStopDelta:
#             print("Stopping early at {}".format(minLossIdx))
#             break
        

        
        
    with open(logname_summary, "a") as file:
            file.write("Summary!\n")
            file.write("Stopped early at {}".format(minLossIdx))
            file.write("\n training Loss:   " + str(training_loss))        
            file.write("\n Validation Loss: " + str(val_loss_set))
            file.write("\n Validation acc:  " + str(val_acc_set))
            file.write("\n Validation iou:  " + str(val_iou_set) + "\n ")
            
        
    #return val_loss_set, val_acc_set, val_iou_set



In [4]:
if __name__=='__main__':
    with open('TrainImageIds.csv', 'r') as f:
        reader = csv.reader(f)
        trainIds = list(reader)[0]
        
#     with open('TestImageIds.csv', 'r') as f:
#         reader = csv.reader(f)
#         testIds = list(reader)[0]
    
    trainIds = [int(i) for i in trainIds]
    #testIds = [int(i) for i in testIds[0]]
    
    # Will shuffle the trainIds incase of ordering in csv
    #random.shuffle(trainIds)
    #splitIdx = int(len(trainIds)/5)
    
    # Selecting 1/5 of training set as validation
    #valIds = trainIds[:splitIdx]
    #trainIds = trainIds[splitIdx:]
    #print(trainIds)
    
    
    trainValRoot = "./data/images/train/"
    #testRoot = "./data/images/test/"
    
    trainValJson = "./data/annotations/captions_train2014.json"
    #testJson = "./data/annotations/captions_val2014.json"
    
    
    with open('./data/vocab.pkl', 'rb') as f:
        vocab = pickle.load(f)
    
    img_side_length = 700
    transform = tf.Compose([
        tf.Resize(img_side_length),
        #tf.RandomCrop(img_side_length),
        tf.CenterCrop(img_side_length),
        tf.ToTensor(),
    ])
    batch_size = 4
    shuffle = True
    num_workers = 1
    
    
    trainDl = get_loader(trainValRoot, trainValJson, trainIds, vocab, 
                         transform=transform, batch_size=batch_size, 
                         shuffle=False, num_workers=1)
#     valDl = get_loader(trainValRoot, trainValJson, valIds, vocab, 
#                          transform=None, batch_size=batch_size, 
#                          shuffle=shuffle, num_workers=1)
#    testDl = get_loader(testRoot, testJson, testIds, vocab, 
#                         transform=None, batch_size=batch_size, 
#                         shuffle=shuffle, num_workers=1)
    
    encoded_feature_dim = 56
    hidden_dim = 50
    
    encoder = Encoder(encoded_feature_dim)
    decoder = Decoder(encoded_feature_dim, hidden_dim, vocab.idx)
    
    criterion = nn.NLLLoss()  # needs softmax before using NLLoss or use crossentorpy instead
    
    epochs = 100
    trainEncoderDecoder(encoder, decoder, criterion, epochs, 
                        trainDl, trainDl, trainDl, "LSTM", batch_size, encoded_feature_dim, vocab.idx)

loading annotations into memory...
Done (t=0.92s)
creating index...
index created!
Loading results to logfile: ./logs/LSTM66.log
Loading Summary to : ./logs/LSTM_summary66.log
DEBUG:  (0, (tensor([[[[0.5608, 0.5647, 0.5686,  ..., 0.5647, 0.5647, 0.5686],
          [0.5569, 0.5569, 0.5647,  ..., 0.5647, 0.5647, 0.5686],
          [0.5569, 0.5569, 0.5608,  ..., 0.5647, 0.5647, 0.5686],
          ...,
          [0.4588, 0.4588, 0.4275,  ..., 0.5137, 0.4980, 0.4941],
          [0.4824, 0.4980, 0.4392,  ..., 0.4824, 0.4980, 0.5451],
          [0.5137, 0.5373, 0.4549,  ..., 0.4588, 0.5059, 0.6039]],

         [[0.6941, 0.6980, 0.7020,  ..., 0.6941, 0.6941, 0.6863],
          [0.6902, 0.6941, 0.6980,  ..., 0.6941, 0.6941, 0.6863],
          [0.6941, 0.6980, 0.6980,  ..., 0.6941, 0.6941, 0.6863],
          ...,
          [0.4549, 0.4706, 0.4510,  ..., 0.5176, 0.5059, 0.5098],
          [0.4784, 0.5098, 0.4667,  ..., 0.4941, 0.5137, 0.5608],
          [0.5059, 0.5373, 0.4784,  ..., 0.4745, 0.52

0it [00:00, ?it/s]

inp shape:  torch.Size([4, 3, 700, 700])
Labels
tensor([[  1,   4,  81,  14, 723, 225,  40,   4, 133,  80,  33, 279,  19,   2,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0],
        [  1,   4,  81,  14, 455, 225,  40,   4, 133,  80,  33, 279,   2,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0],
        [  1,   4, 331,  14,  52,  77,  40,   4, 265, 133,   2,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0],
 

2it [00:00,  2.68it/s]

epoch0, iter0, loss: -0.7143159508705139
inp shape:  torch.Size([4, 3, 700, 700])
Labels
tensor([[   1,   74,  455,  225,   40,    4,  133,  102,    4, 1813,   19,    2,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0],
        [   1,    4,  179, 2479,  171,   40,    4, 1342,  124,  205,   19,    2,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0],
        [   1,    4,  336, 2479,   65,  131,   78,  252,  124,  137,    2,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    

...

tensor([[1, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4],
        [1, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4],
        [1, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4],
        [1, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4]], device='cuda:0')
test pred:  tensor([[1, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 

10it [00:02,  4.71it/s]

test pred:  tensor([[1, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4],
        [1, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4],
        [1, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4],
        [1, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4]], device='cuda:0')
test pred shape:  torch.Size([4, 56])
sentence shape:  torch.Size([4, 56])
features size:  torch.Size([4, 56])
embeds size:  torch.Size([4, 56, 56])
lengths:  (12, 17, 13, 15)
lstm inp s

i:  0
imgs:  tensor([[[[0.5608, 0.5647, 0.5686,  ..., 0.5647, 0.5647, 0.5686],
          [0.5569, 0.5569, 0.5647,  ..., 0.5647, 0.5647, 0.5686],
          [0.5569, 0.5569, 0.5608,  ..., 0.5647, 0.5647, 0.5686],
          ...,
          [0.4588, 0.4588, 0.4275,  ..., 0.5137, 0.4980, 0.4941],
          [0.4824, 0.4980, 0.4392,  ..., 0.4824, 0.4980, 0.5451],
          [0.5137, 0.5373, 0.4549,  ..., 0.4588, 0.5059, 0.6039]],

         [[0.6941, 0.6980, 0.7020,  ..., 0.6941, 0.6941, 0.6863],
          [0.6902, 0.6941, 0.6980,  ..., 0.6941, 0.6941, 0.6863],
          [0.6941, 0.6980, 0.6980,  ..., 0.6941, 0.6941, 0.6863],
          ...,
          [0.4549, 0.4706, 0.4510,  ..., 0.5176, 0.5059, 0.5098],
          [0.4784, 0.5098, 0.4667,  ..., 0.4941, 0.5137, 0.5608],
          [0.5059, 0.5373, 0.4784,  ..., 0.4745, 0.5255, 0.6196]],

         [[0.8275, 0.8353, 0.8392,  ..., 0.8314, 0.8314, 0.8275],
          [0.8275, 0.8314, 0.8353,  ..., 0.8314, 0.8314, 0.8275],
          [0.8275, 0.8314, 0.

VAL: loss_avg:  tensor(-0.7469, device='cuda:0')
VAL: bleu4_avg:  6.659801989051833e-232
VAL: bleu1_avg:  0.01785714285714285


In [5]:
%debug

ERROR:root:No traceback has been produced, nothing to debug.
